# This is a tutorial for how to extract data from Scifeon into python.

By Troels Angelo: <angelo@scifeon.com>

The script is split into pieces of code to make it easier to run.
To run this script you'll need to install the requests library, this can be done by:


`pip install --upgrade requests`

If you are using conda to run your notebook, then you should use following code to install it:

`conda install --upgrade requests`

Import the following libraries:

In [ ]:
import requests
import json

Now that requests is installed we can run the script, in order to make the script run you'll need to provide your scifeon cloud domain, your username and password. Please keep the " ":

In [ ]:
scifeonCloudDomain = "Insert you domian.scifeon.cloud here"
username = "Insert your username"
password = "Insert your password"

These values are now used in the following script to generate an access_token:

In [ ]:
rqheader = {"Content-Type": "application/json"}

urltoken="https://"+scifeonCloudDomain+"/api/auth/login"

response=requests.request("POST", urltoken,
    json={
        "username": username,
        "password": password},
    headers = rqheader)

r = response.json()

access_token = r.get('accessToken')

An access_token is now made and you can extract your data, here you need to provide the entity of interest. 
If this for example is an experiment it should be put like entity/experiment/experimentID as seen in the example below.

In [ ]:
urlcontent = "https://" + scifeonCloudDomain + "/api/entity/experiment/EX00001" #Swap /experiment/EX00001 with entity of interest

getheaders = {
 "Authorization": "Bearer " + access_token,
 "Content-Type": "application/json"
 }

r = requests.get(urlcontent, headers=getheaders)

files = r.json()

The "files" will now contain a dictionary of the given entity. This can be read in JSON structure by running the following script:

In [ ]:
def jprint(obj):
    # create a formatted string of the Python JSON object
    text = json.dumps(obj, sort_keys=True, indent=4)
    print(text)

jprint(files)

Furthermore, if you are interested in running a datasetQuery, this can be done with following example, where resultvalues for the fermentation FRM2856 is extracted:

In [ ]:
urlcontent = "https://" + scifeonCloudDomain + "/api/query/dataset"

getheaders = {
 "Authorization": "Bearer " + access_token,
 "Content-Type": "application/json"
 }

parameters = [
            {
                "eClass": "Sample", "collection": "samples",
                "filters": [
                    { "field": "FermentationID", "value": "FRM2856"},
                    { "field": "dtiTaken", "op": "isnotnull" },
                ],
            },
            {
                "eClass": "ResultValue", "collection": "resultValues",
                "filters": [{ "field": "SubjectID", "in": "samples.ID" }],
                "select": ["subjectID", "resultSetID", "type", "unit", "valueFloat"],
            }]

rdata = requests.request("POST", urlcontent, headers=getheaders, json=parameters)

files = rdata.json()

jprint(files)

Files will be a dictionary containing the extracted information.
Multiple samples can be queryed using a loop:

In [ ]:
fermentations = ["FRM2856", "FRM2857"]
rdata = []
files = []

urlcontent = "https://" + scifeonCloudDomain + "/api/query/dataset"

for fermentation in fermentations:
    getheaders = {
    "Authorization": "Bearer " + access_token,
    "Content-Type": "application/json"
    }

    parameters = [
                {
                    "eClass": "Sample", "collection": "samples",
                    "filters": [
                        { "field": "FermentationID", "value": fermentation},
                        { "field": "dtiTaken", "op": "isnotnull" },
                    ],
                },
                {
                    "eClass": "ResultValue", "collection": "resultValues",
                    "filters": [{ "field": "SubjectID", "in": "samples.ID" }],
                    "select": ["subjectID", "resultSetID", "type", "unit", "valueFloat"],
                }]

    rdata.append(requests.request("POST", urlcontent, headers=getheaders, json=parameters))

for data in rdata:
    files.append(data.json())

jprint(files)

Files will contain a list of dictionaries.

You can find you documentation for datasetQueries [here](https://docs.scifeon.com/developer/reference/http-api/endpoints/query#dataset)

If you are interested in saving your edits on the data at the server. It can be done using the following script:

## A single file

In [ ]:
urlcontent = "https://" + scifeonCloudDomain + "/api/entity"

getheaders = {
    "Authorization": "Bearer " + access_token,
    "Content-Type": "application/json"
            }

parameters = {
                 "entities": [files]
            }
                
    requests.request("POST", urlcontent, headers = getheaders, json = parameters)

## Multiple files

In [ ]:
urlcontent = "https://" + scifeonCloudDomain + "/api/entity"

getheaders = {
    "Authorization": "Bearer " + access_token,
    "Content-Type": "application/json"
            }

for i in range(len(files)):
    parameters = {
                     "entities": [files[i]]
                }
                
    requests.request("POST", urlcontent, headers = getheaders, json = parameters)

Just be aware that access tokens only have a lifetime of 20 minuttes so there might need to be generated some new ones.